In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import json
import re
from tqdm import tqdm # 用於顯示進度條
import csv

# --- 1. 常數與提示詞定義 (來自您的 GRPO 腳本) ---

SYSTEM_PROMPT = """你是一名專門根據患者用藥與病史紀錄預測 ICD-10 編碼的醫學專家。  
請嚴格遵守以下作答格式：  

<reasoning>  
逐步推理：逐條說明病例中每個臨床資訊（症狀、診斷、檢查結果、既往病史、用藥等）可能對應的 ICD-10 編碼，並在最後總結出最合理的編碼集合。  
</reasoning>  
<answer>  
僅輸出最終的 ICD-10 編碼，使用英文逗號分隔，不要添加任何額外文字或解釋。  
</answer>  
"""

EXAMPLE_QUESTION = """
Sex: F
Service: MEDICINE
Allergies: Aspirin
Attending: ___
Chief Complaint: weakness, diarrhea
Major Surgical or Invasive Procedure: None

History of Present Illness:
Ms. ___ is a ___ year-old woman with PMH significant for chronic anemia, osteoporosis, hypertension, ataxia, and recent L5 fracture in the setting of recurrent falls who presents from home with fatigue and generalized weakness and diarrhea.  

The patient's recent history is notable for the follow:  
- On ___, she presented with 4 days of LBP s/p fall from standing at which time imaging revealed acute L5 fracture. She was evaluated by Spine team who recommended early mobilization, pain control, but no brace required. She was evaluated by ___, and discharged to ___.  
- She was discharged home with ___ on ___.  
- On ___, she again presented to ___ s/p fall from standing while trying to reach for a glass of water. She did have a occipital scalp hematoma, but imaging including ___, C-spine CT, and L hip X-ray were negative for acute process so patient was discharged home.  

She now represents with generalized fatigue and diarrhea. In the setting of opiates for her L5 fracture, the patient has had constipation (5 days with no BM) for which she took a "natural laxative" the evening prior to presentation. The patient had 2 bowel movements in the morning of presentation and one episode of incontinence with diarrhea while sleeping. In this setting, she felt very weak and called EMS and was brought to ___ ED.

What ICD-10 codes should be assigned? Please just tell me which codes in the end
"""
EXAMPLE_REASONING = """The patient has chronic anemia, documented and clinically relevant, which corresponds to D500.  
There is vitamin deficiency suggested, which fits E538.  
She also has visual impairment history, which maps to H548.  
Hypertension is a chronic condition, coded as I10.  
Diarrhea due to laxative use is coded as K521 (toxic gastroenteritis and colitis).  
Her recent fracture with underlying osteoporosis corresponds to M810.  
Ataxia is a chronic neurologic condition, coded as R270.  
There is adverse effect of drugs (laxatives/opioids), so T474X5A applies.  
Environmental factor of injury is Y92099 (unspecified place of occurrence).  
She also has aspirin allergy, captured by Z9181.  

Therefore, the most appropriate ICD-10 codes are:
</reasoning>
"""

EXAMPLE_ANSWER = "D500 E538 H548 I10 K521 M810 R270 T474X5A Y92099 Z9181"

/mnt/data2/icd10/venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
def extract_icd_answer(text: str) -> str:
    """
    從模型的完整回覆或標準答案中提取 ICD-10 編碼。
    優先從 <answer> 標籤中提取,若無則從整個文本中提取。
    """
    # 使用正則表達式搜尋 <answer> 標籤，re.DOTALL 讓 . 可匹配換行符，re.IGNORECASE 忽略大小寫
    answer_match = re.search(r'<answer>(.*?)</answer>', text, re.DOTALL | re.IGNORECASE)
    # 如果找到 <answer> 標籤，則只在標籤內容中搜尋 ICD 編碼；否則在整個文本中搜尋
    search_text = answer_match.group(1) if answer_match else text
    
    # 匹配格式：字母 + 1-3位數字 + 可選的小數點和1-2位數字
    codes_list = re.findall(r'\b([A-Z]\d{1,6}(?:\.\d{1,2})?)\b', search_text, re.IGNORECASE)
    
    # 移除小數點、去重、排序、轉大寫，並過濾掉長度<=2的編碼
    cleaned_codes = sorted(set(
        code.replace('.', '').upper() 
        for code in codes_list 
        if len(code.replace('.', '')) > 2
    ))
    return " ".join(cleaned_codes)



def extract_xml_answer(text: str) -> str:
    """提取 <answer> 標籤內的內容"""
    answer = text.split("<answer>")[-1]
    answer = answer.split("</answer>")[0]
    answer = answer.strip()
    return answer


def is_text(text: str) -> bool:
    """判斷輸入字串是否主要為文字敘述（而非 ICD code 等短編碼）"""
    letters_and_spaces = sum(c.isalpha() or c.isspace() for c in text)
    ratio = letters_and_spaces / max(1, len(text))  
    return ratio > 0.5


def compute_f1(pred: str, true: str) -> float:
    """
    計算 F1 分數 (前三個字符匹配即算正確)
    
    Args:
        pred: 預測的 ICD 編碼字串,例如 "A010 B021"
        true: 真實的 ICD 編碼字串,例如 "A010 C032"
    
    Returns:
        F1 分數 (0.0 到 1.0)
    """
    # 將字串轉換為 set
    pred = pred.replace('.', '')
    true = true.replace('.', '')
    
    def parse_codes(text):
        if ',' in text:
            return set(code.strip().upper() for code in text.split(',') if code.strip())
        else:
            return set(code.strip().upper() for code in text.split() if code.strip())
    
    pred_set = parse_codes(pred)
    true_set = parse_codes(true)
    
    # 如果都是空集合,視為完全匹配
    if not pred_set and not true_set:
        return 1.0
    
    # 轉換為前三個字符的集合
    def get_prefix_set(codes):
        return set(code[:3] for code in codes if len(code) >= 3)
    
    pred_prefix = get_prefix_set(pred_set)
    true_prefix = get_prefix_set(true_set)
    
    # 計算 TP, FP, FN
    tp = len(pred_prefix & true_prefix)
    fp = len(pred_prefix - true_prefix)
    fn = len(true_prefix - pred_prefix)
    
    precision = tp / (tp + fp) if (tp + fp) > 0 else 0.0
    recall = tp / (tp + fn) if (tp + fn) > 0 else 0.0
    
    if precision + recall == 0:
        return 0.0
    
    f1 = 2 * precision * recall / (precision + recall)
    print(f"✅ Precision: {precision:.4f}, Recall: {recall:.4f}, F1: {f1:.4f}")
    return f1



def count_xml(text: str) -> float:
    """
    檢查 XML 標籤格式的完整性
    
    Returns:
        分數 (0.0 到 0.5),分數越高表示格式越完整
    """
    score = 0.0
    
    if text.count("<reasoning>\n") == 1:
        score += 0.125
    if text.count("\n</reasoning>\n") == 1:
        score += 0.125
    if text.count("\n<answer>\n") == 1:
        score += 0.125
        # 懲罰 </answer> 後有多餘內容
        extra_content = len(text.split("\n</answer>\n")[-1])
        score -= extra_content * 0.001
    if text.count("\n</answer>") == 1:
        score += 0.125
        # 懲罰 </answer> 後有多餘內容
        extra_content = len(text.split("\n</answer>")[-1]) - 1
        score -= max(0, extra_content) * 0.001
    
    return max(0.0, score)  # ✅ 確保不會是負數

In [ ]:
# --- 3. 載入模型與 Tokenizer ---
model_path = "./models/Qwen3-14B-FP8" 

print(f"正在載入模型: {model_path} ...")
tokenizer = AutoTokenizer.from_pretrained(model_path)
model = AutoModelForCausalLM.from_pretrained(
    model_path,
    torch_dtype=torch.bfloat16,
    device_map="auto",
    attn_implementation="flash_attention_2"
)

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
print("模型載入完畢。")

# --- 4. 載入並處理資料 ---

print("正在載入 note_icd_data.jsonl ...")
chat_style_data = []
try:
    with open("note_icd_data.jsonl", "r", encoding="utf-8") as f:
        for i, line in enumerate(f):
            if i >= 715:
                print(f"已讀取前 {i} 筆資料 (上限 10 筆)。")
                break
            
            item = json.loads(line)  
            
            chat_prompt = [
                {"role": "system", "content": SYSTEM_PROMPT},
                {"role": "user", "content": EXAMPLE_QUESTION},
                {"role": "assistant", "content": f"<reasoning>{EXAMPLE_REASONING}</reasoning><answer>{EXAMPLE_ANSWER}</answer>"},
                {"role": "user", "content": item["question"]}
            ]
            
            ground_truth_answer= extract_icd_answer(item["answer"])
            
            chat_style_data.append({
                "prompt": chat_prompt,
                "answer": ground_truth_answer,
                "raw_question": item["question"]
            })
except FileNotFoundError:
    print("錯誤：找不到 'note_icd_data.jsonl' 檔案。")
    exit()

print(f"資料載入完畢，共 {len(chat_style_data)} 筆。")

正在載入模型: ./models/Qwen3-14B-FP8 ...


Loading checkpoint shards: 100%|██████████| 4/4 [00:02<00:00,  1.57it/s]


模型載入完畢。
正在載入 note_icd_data.jsonl ...
資料載入完畢，共 3852 筆。


In [ ]:
# --- 5. 執行 Baseline 推論並計算所有指標 ---
# 用於 Baseline Micro-F1
all_predictions_baseline = []
all_ground_truths_baseline = []
all_acc_baseline = []
all_strict_baseline = []
all_completion_lengths = []

# === 新增：初始化 CSV 檔案,寫入表頭 ===
csv_filename = "qwen_baseline_14B_v2.csv"
with open(csv_filename, 'w', newline='', encoding='utf-8') as f:
    fieldnames = ['accuracy_reward', 'completion_length', 'ground_truths_ans', 'predictions_ans']
    writer = csv.DictWriter(f, fieldnames=fieldnames)
    writer.writeheader()

print(f"📁 CSV 檔案已初始化: {csv_filename}\n")

with torch.no_grad():
    for idx, item in enumerate(tqdm(chat_style_data, desc="[Baseline] 執行推論與評估"), 1):
        chat_prompt = item["prompt"]
        gt_answer = item["answer"]
        
        try:
            prompt_str = tokenizer.apply_chat_template(
                chat_prompt, 
                tokenize=False, 
                add_generation_prompt=True
            )
        except Exception as e:
            # 手動回退格式 (適用於 MedGemma)
            print(f"手動回退格式: {e}")
            prompt_str = (
                f"<start_of_turn>system\n{chat_prompt[0]['content']}<end_of_turn>\n"
                f"<start_of_turn>user\n{chat_prompt[1]['content']}<end_of_turn>\n"
                f"<start_of_turn>model\n{chat_prompt[2]['content']}<end_of_turn>\n"
                f"<start_of_turn>user\n{chat_prompt[3]['content']}<end_of_turn>\n"
                f"<start_of_turn>model\n"
            )
        
        inputs = tokenizer(
            prompt_str, 
            return_tensors="pt", 
            max_length=4096,
            truncation=True
        ).to(model.device)
        
        outputs = model.generate(
            **inputs,
            max_new_tokens=2000,
            do_sample=False,
            pad_token_id=tokenizer.eos_token_id
        )
        
        input_length = inputs.input_ids.shape[1]
        generated_tokens = outputs[0][input_length:]
        assistant_reply = tokenizer.decode(generated_tokens, skip_special_tokens=True)
        
        # === 印出完整資訊 ===
        print("\n" + "="*80)
        print(f"📝 樣本 #{idx}")
        print("="*80)
        print(f"\n🤖 模型完整回答:")
        print("-"*80)
        print(assistant_reply)
        print("-"*80)
        
        all_ground_truths_baseline.append(gt_answer)
        
        # 記錄 completion length (token 數)
        completion_length = len(generated_tokens)
        print(f"\n📊 完成的回覆長度 (token 數): {completion_length}")
        all_completion_lengths.append(completion_length)
        
        # 計算 Baseline metrics
        predicted_codes_baseline = extract_icd_answer(assistant_reply)
        print(f"🔍 提取的 ICD-10 編碼: {predicted_codes_baseline}")
        all_predictions_baseline.append(predicted_codes_baseline)

        print(f"\n🎯 Ground Truth Answer:")
        print(f"   {gt_answer}")
        
        acc_baseline = compute_f1(predicted_codes_baseline, gt_answer)
        print(f"✅ Baseline F1 分數: {acc_baseline:.4f}")
        all_acc_baseline.append(acc_baseline)
        
        
        with open(csv_filename, 'a', newline='', encoding='utf-8') as f:
            writer = csv.DictWriter(f, fieldnames=fieldnames)
            writer.writerow({
                'accuracy_reward': acc_baseline,
                'completion_length': completion_length,
                'ground_truths_ans': gt_answer,
                'predictions_ans': predicted_codes_baseline
            })
        
        print(f"💾 結果已儲存至 {csv_filename} (第 {idx} 筆)")
        print("="*80 + "\n")

print("\n" + "="*80)
print("🎉 推論完成!")
print("="*80)

# --- 6. 顯示最終統計 ---
if not all_predictions_baseline:
    print("沒有可評估的結果。")
else:
    print("\n" + "="*50)
    print("  Baseline (medgemma-4b-it) 最終統計")
    print("="*50)
    print(f"✅ 總共處理: {len(all_acc_baseline)} 筆資料")
    print(f"📊 平均 F1 分數: {sum(all_acc_baseline)/len(all_acc_baseline):.4f}")
    print(f"📏 平均回覆長度: {sum(all_completion_lengths)/len(all_completion_lengths):.1f} tokens")
    print(f"💾 結果已完整儲存至: {csv_filename}")
    print("="*50)

📁 CSV 檔案已初始化: qwen_baseline_14B.csv



[Baseline] 執行推論與評估:   0%|          | 1/3852 [02:41<173:08:28, 161.86s/it]The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



📝 樣本 #1

🤖 模型完整回答:
--------------------------------------------------------------------------------
<think>
Okay, let's tackle this ICD-10 coding for patient 2000024. First, I need to go through the medical record carefully. The patient is a female with several chronic conditions mentioned in her PMH: chronic anemia, osteoporosis, hypertension, ataxia, and a recent L5 fracture from recurrent falls. The chief complaints are weakness and diarrhea.

Starting with the chronic anemia. The lab results show Hct 25.4, which is low, and the iron studies are within normal range. The diagnosis here is likely chronic anemia, which would be coded as D50.0 for anemia due to chronic disease. Wait, but the patient has a history of chronic anemia, so maybe D50.0 is appropriate. However, if the anemia is due to another condition, like the L5 fracture or something else, but the PMH states it's chronic, so D50.0 makes sense.

Next, osteoporosis. The patient has a recent L5 fracture, which is a result of 

[Baseline] 執行推論與評估:   0%|          | 2/3852 [05:18<169:56:12, 158.90s/it]The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



📝 樣本 #2

🤖 模型完整回答:
--------------------------------------------------------------------------------
<think>
Okay, let's tackle this ICD-10 coding for the patient with cardiogenic shock. First, I need to go through the history of present illness and other details carefully.

The patient is a male with a history of 3-vessel CAD and RCA stenting, ischemic cardiomyopathy with an ejection fraction of 25%, which is a key point. That's a chronic condition, so I should code I51.4 for ischemic cardiomyopathy. The EF of 25% is significant for heart failure with reduced ejection fraction, which would be I50.21.

He has DMII, so E11.9. Hypertension is mentioned as HLD, which I think stands for hypertension, so I10.9. Obesity is Z87.89, but wait, the current condition is obesity, so maybe Z87.89 is for a history of obesity, but the patient has obesity as a PMH. Wait, the PMH includes obesity, so maybe Z87.89 is for a history of obesity. But if the patient currently has obesity, it's Z87.89. Hmm, n

...


📝 樣本 #713

🤖 模型完整回答:
--------------------------------------------------------------------------------
<think>
Okay, let's tackle this ICD-10 coding for the patient's case. First, I need to go through the history of present illness and other details to identify all relevant diagnoses and conditions.

The patient is a female with a chief complaint of dizziness. The main issues mentioned are vertigo, hyponatremia, and a history of exertional chest pain. Let's break it down step by step.

Starting with the vertigo. The patient has had intermittent vertigo for a week, which started after a dilated eye exam for posterior vitreous separation. The PCP diagnosed vestibular neuritis, which is a common cause of vertigo. So, ICD-10 code for vestibular neuritis is H81.01 (right-sided) or H81.02 (left-sided). Since the nystagmus was predominantly right-sided, H81.01 would be appropriate.

Next, the hyponatremia. The lab result was Na 126, which is definitely hyponatremia. The code for this is E86.0

[Baseline] 執行推論與評估:  19%|█▊        | 714/3852 [22:45:19<100:14:21, 115.00s/it]The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



📝 樣本 #714

🤖 模型完整回答:
--------------------------------------------------------------------------------
<think>
Okay, let's tackle this ICD-10 coding for the patient. First, I need to go through the provided medical record step by step.

The patient is male, and the service is Otolaryngology. His allergies are penicillins, which would be Z88.0. The chief complaints are dysphagia, esophageal mass, and vocal cord hypomobility. The major procedures done were direct laryngoscopy (DL), esophagoscopy, and biopsy of the cricopharyngeal mass.

Starting with the chief complaints. Dysphagia is a common symptom, and the ICD-10 code for dysphagia is K92.0. However, since the patient has an esophageal mass, that might be the underlying cause. The mass at the cricopharyngeus is likely a neoplasm, so I need to check the code for that. The code for a benign neoplasm of the cricopharyngeus would be D32.1, but if it's malignant, it would be C32.1. The problem doesn't specify if it's benign or malignant, 

[Baseline] 執行推論與評估:  19%|█▊        | 714/3852 [22:45:57<100:03:20, 114.79s/it]


KeyboardInterrupt: 